In [29]:
# Import
import time 
import sys
import numpy as np
import argparse
import string
import concurrent
from concurrent.futures import ProcessPoolExecutor, ThreadPoolExecutor, Future, as_completed, wait

# Webscraping Imports
from bs4 import BeautifulSoup, SoupStrainer
from urllib.request import urlopen
from urllib.error import URLError, HTTPError
import grequests

# Viualization Imports
import networkx as nx
import matplotlib.pyplot as plt

In [30]:
#Grequest Exception Handler
def exception_handler(request, exception):
    print(request.text)
    print("Request failed")

In [31]:
# Tree Visualization
G = nx.DiGraph()

# Changable Variables
USE_THREADPOOL = False
MAKE_GRAPH = True

In [32]:
# Dismissed links are links shared by all sites and do not factor into 6 degrees of separation
dismissed_links = ["Talk", "Categories", "Contributions", "Article", "Read", "Main page", "Contents", "Current events", "Random article", "About Wikipedia", "Help", "Community portal", "Recent changes", "Upload file", "What links here", "Related changes", "Upload file", "Special pages", "About Wikipedia", "Disclaimers", "Articles with short description", "Short description matches Wikidata", "Wikipedia indefinitely semi-protected biographies of living people", "Use mdy dates from October 2016", "Articles with hCards", "BLP articles lacking sources from October 2017", "All BLP articles lacking sources", "Commons category link from Wikidata", "Articles with IBDb links", "Internet Off-Broadway Database person ID same as Wikidata", "Short description is different from Wikidata", "PMID", "ISBN", "doi"] 
degree = 0
path = []
path_found = False
current_generation = []
child_generation = []

In [33]:
# Configure args.fromtitle and args.totitle
fromtitle = "KEVIN bacon"
fromtitle = string.capwords(fromtitle.lower()).replace(" ", "_")
totitle = "neo-nOIR"
totitle = string.capwords(totitle.lower()).replace(" ", "_")

In [34]:
# BS4 optimization
only_a_tags = SoupStrainer("a", href=lambda href: href and href.startswith('/wiki/'))

In [35]:
# Define Node
class Node:
    def __init__(self, title, url):
        self.title = title
        self.url = url
        self.parent = None
        self.children = []
        self.searched = False

    def get_url(self):
        return self.url

# find_children - A function that returns all relevant referrals by Wikipedia
def find_children(resp):
    global USE_THREADPOOL
    children = []
    for r in resp:
        soup = BeautifulSoup(r.text, "lxml", parse_only = only_a_tags)
        soup = soup.find_all("a")
        for entry in soup:
            if str(entry.get('title')) != "[]":
                if "/wiki/Help:" in entry.get('href') or entry.get('title') == None or "Wikipedia articles with" in entry.get('title') or "[<" in entry.get('title') or "<" in str(entry.get('href')):
                    continue
                else:
                    if entry.get('title') in dismissed_links:
                        continue
                    # If relevant, add to entries
                    child_node = Node(entry.get('title'),"https://en.wikipedia.org" + entry["href"])
                    # Visualization
                    children.append(child_node)
    return children

In [36]:
def attempt_match_children(current_node, to_node):
    global child_generation
    global path 
    global path_found
    global USE_THREADPOOL

    current_node.searched = True
    # Check children for any matches w/ to_node 
    for child_node in current_node.children:
        # Check if child_node was already searched
        if child_node.searched == False:
            # Add child_node to new generation
            child_generation.append(child_node)
            # If child_node is the to_node, search is over
            if child_node.url == to_node.url:
                path.append(current_node)
                path.append(child_node)
                path_found = True
                return True
    return False

In [37]:
# Determine amount of degrees and commonalities, with origin and end being urls
def determine_path(from_node, to_node):
    global path_found
    global current_generation
    global path
    global degree
    global child_generation 
    global USE_THREADPOOL

    # 0th degree
    if from_node.url == to_node.url:
        path_found == True
        return path

    # 1st degree
    degree += 1
    resp = urlopen(from_node.url)
    soup = BeautifulSoup(resp, 'html.parser', parse_only = only_a_tags)
    for entry in soup:
            if str(entry.contents) != "[]":
                if "/wiki/Help:" in entry.contents[0] or "Wikipedia articles with" in entry.contents[0] or "[<" in entry.contents[0] or "<" in str(entry.contents[0]) or entry.contents[0] == None:
                    continue
                else:
                    if entry.contents[0] in dismissed_links:
                        continue
                    # If relevant, add to entries
                    child_node = Node(entry.contents[0],"https://en.wikipedia.org" + entry["href"])
                    # Visualization
                    from_node.children.append(child_node)
    attempt_match_children(from_node, to_node)

    # 2+ degree: if none of the children match, continue to search through loop
    if path_found == False:
        current_node = from_node
        current_generation = current_node.children
        path.append(current_node)
        
        while path_found == False: 
            print("degree raised heh")
            degree += 1
            child_generation = []
            '''# Special Threadpool to find children: attempt to stop bottleneck
            if USE_THREADPOOL == True:
                with ThreadPoolExecutor(max_workers=4) as executor:
                    [executor.map(sibling_node.find_children()) for sibling_node in current_generation]
            '''
            
            # Use G-requests to speed up url opening for response
            rs = [grequests.get(sibling_node.url, params = sibling_node.url) for sibling_node in current_generation]
            resp = grequests.map(rs, exception_handler=exception_handler)
            current_generation = find_children(resp)
            
            # Keep Looping through each sibling_node and check sibling's children
            for sibling_node in current_generation:
                if sibling_node.searched == False:
                    attempt_match_children(sibling_node, to_node)
                    # If found match in current degree
                    if path_found == True:
                        return sibling_node
            # If none of the siblings in the level matched, move to higher degree
            if path_found == False:
                current_generation = child_generation
                child_generation = []
    return path

In [38]:
def main():
    global current_generation
    start = time.time()

    #root = Node("Kevin Bacon", "https://en.wikipedia.org/wiki/Kevin_Bacon")
    #target = Node("Neo-noir", "https://en.wikipedia.org/wiki/Hollywood")

    # Find/Check Valid Root and Target URL
    try: 
        urlopen("https://en.wikipedia.org/wiki/" + fromtitle)
        print("https://en.wikipedia.org/wiki/" + fromtitle)
        print("https://en.wikipedia.org/wiki/" + totitle)
        urlopen("https://en.wikipedia.org/wiki/" + totitle)
    except HTTPError:
        print("HTTPError: Invalid Name")
        sys.exit(1)
    except URLError:
        print("URLError: Invalid Name")
        sys.exit(1)
    except ValueError:
        print("ValueError: Invalid Name")
        sys.exit(1)

    root = Node(fromtitle.title(), "https://en.wikipedia.org/wiki/" + fromtitle)
    target = Node(totitle.title(), "https://en.wikipedia.org/wiki/" + totitle)
    
    current_generation.append(root)
    determine_path(root, target)
    
    # Present Data
    path_names = []
    for node in path:
        path_names.append(node.title)
    print(time.time() - start)
    print("Path: " + str(path_names))
    print("Degree: " + str(degree))

    # Visualization of Path
    if MAKE_GRAPH:
        for i, node in enumerate(path):
            G.add_node(node.title)
            if i > 0:
                G.add_edge(path[i-1].title, node.title)
            print(node.url)
        nx.draw(G, with_labels=True)
        plt.show()

In [39]:
if __name__ == '__main__':
    main()

https://en.wikipedia.org/wiki/Kevin_Bacon
https://en.wikipedia.org/wiki/Neo-noir
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
d

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

...

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree raised heh
degree rai

KeyboardInterrupt: 